In [1]:
!pip install imutils

In [2]:
import pandas as pd
import numpy as np
import os
from tqdm import tqdm
from PIL import Image
import requests
from io import BytesIO
from imutils import build_montages
from imutils import paths
import cv2

In [3]:
collections = pd.read_csv("collections.csv")
datasets = []
dataset_len = {}

for dataset_name,i in zip(collections['symbol'],range(len(os.listdir('Collections')))):
    dataset_name = pd.read_csv("Collections/"+dataset_name+".csv")
    dataset_name['collectionsImage']= collections.iloc[i, collections.columns.get_loc('image')]
    dataset_name['collectionCreatedAt']=  collections.iloc[i, collections.columns.get_loc('createdAt')]
    dataset_name['collectionUpdatedAt'] = collections.iloc[i, collections.columns.get_loc('updatedAt')]
    for col in ['candyMachineIds','categories', 'description', 'enabledAttributesFilters','isDraft', 'website', 'twitter', 'discord', 'derivativeDetails','isDerivative', 'nftImageType', 'totalItems', '__v','flagMessage', 'isFlagged', 'rarity']:
        dataset_name[col] = collections.iloc[i, collections.columns.get_loc(col)]
    datasets.append(dataset_name)

In [4]:
df = pd.concat(datasets)
df.shape

(36382, 44)

In [5]:
df.to_csv('out.csv')

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 36382 entries, 0 to 87
Data columns (total 44 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   Unnamed: 0                36382 non-null  int64  
 1   id                        36382 non-null  object 
 2   price                     36382 non-null  float64
 3   escrowPubkey              36382 non-null  object 
 4   owner                     36382 non-null  object 
 5   collectionName            36382 non-null  object 
 6   collectionTitle           36382 non-null  object 
 7   img                       36382 non-null  object 
 8   title                     36382 non-null  object 
 9   content                   33238 non-null  object 
 10  propertyCategory          33848 non-null  object 
 11  creators                  36382 non-null  object 
 12  sellerFeeBasisPoints      36382 non-null  int64  
 13  mintAddress               36382 non-null  object 
 14  attribute

write description for each feature - Linor <br>

fill up the followers count on SM - Yonatan <br>
decide on what columns should be dropped <br>
fix date column - tamar <br>
import economic features - solana, nft trade volume by week/day, exchange comissions, time from creation to sell - marian <br>
extract visual features - tamar <br>
merging data sources into one dataset - Yonatan  <br>


In [7]:
'''
import configparser
from tweepy import API, Cursor, OAuthHandler, TweepError
# Read in configs
configs = configparser.ConfigParser()
configs.read('./config.ini')
keys = configs['TWITTER']
consumer_key = keys['CONSUMER_KEY'] 
consumer_secret = keys['CONSUMER_SECRET'] 
access_token = keys['ACCESS_TOKEN']
access_secret = keys['ACCESS_SECRET']
# Authenticate Tweepy connection to Twitter API
auth = OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token, access_secret)
api = API(auth, wait_on_rate_limit=True, wait_on_rate_limit_notify=True)
user = api.get_user(screen_name='psykergame')
print(user.followers_count)
'''

"\nimport configparser\nfrom tweepy import API, Cursor, OAuthHandler, TweepError\n# Read in configs\nconfigs = configparser.ConfigParser()\nconfigs.read('./config.ini')\nkeys = configs['TWITTER']\nconsumer_key = keys['CONSUMER_KEY'] \nconsumer_secret = keys['CONSUMER_SECRET'] \naccess_token = keys['ACCESS_TOKEN']\naccess_secret = keys['ACCESS_SECRET']\n# Authenticate Tweepy connection to Twitter API\nauth = OAuthHandler(consumer_key, consumer_secret)\nauth.set_access_token(access_token, access_secret)\napi = API(auth, wait_on_rate_limit=True, wait_on_rate_limit_notify=True)\nuser = api.get_user(screen_name='psykergame')\nprint(user.followers_count)\n"

Extarcting Visual Features

In [8]:
def image_colorfulness(image):
	# split the image into its respective RGB components
	(B, G, R) = cv2.split(image.astype("float"))
	# compute rg = R - G
	rg = np.absolute(R - G)
	# compute yb = 0.5 * (R + G) - B
	yb = np.absolute(0.5 * (R + G) - B)
	# compute the mean and standard deviation of both `rg` and `yb`
	(rbMean, rbStd) = (np.mean(rg), np.std(rg))
	(ybMean, ybStd) = (np.mean(yb), np.std(yb))
	# combine the mean and standard deviations
	stdRoot = np.sqrt((rbStd ** 2) + (ybStd ** 2))
	meanRoot = np.sqrt((rbMean ** 2) + (ybMean ** 2))
	# derive the "colorfulness" metric and return it
	return stdRoot + (0.3 * meanRoot)
def brightness(img):
    return img.mean()


In [9]:
df['img colorfulness'] = np.nan
df['img brightness'] = np.nan

In [ ]:
for index, row in tqdm(df.iterrows()):
    try:
        response = requests.get(df.iloc[index, df.columns.get_loc('img')])
        img = Image.open(BytesIO(response.content)).convert('RGB') 
        data = np.array(img, dtype=np.float32) 
        # Convert RGB to BGR 
        data = data[:, :, ::-1].copy()
        df.iloc[index,df.columns.get_loc('img colorfulness')] = image_colorfulness(data)
        df.iloc[index,df.columns.get_loc('img brightness')]= brightness(data)
        print("success",df.iloc[index, df.columns.get_loc('img')] )
    except:
        print("failed", df.iloc[index, df.columns.get_loc('img')])

1it [00:00,  1.08it/s]

success https://gldhero-production.s3.amazonaws.com/4857.png


2it [00:01,  1.11it/s]

success https://gldhero-production.s3.amazonaws.com/2279.png


3it [00:02,  1.16it/s]

...

success https://gldhero-production.s3.amazonaws.com/3097.png


32982it [9:17:42,  1.01it/s]

success https://gldhero-production.s3.amazonaws.com/2529.png


32983it [9:17:43,  1.01it/s]

success https://gldhero-production.s3.amazonaws.com/5994.png


In [11]:
df.to_csv('out1.csv')


In [12]:
#import libraries used below
import requests
import os
import json
import pandas as pd
import csv
import datetime
import dateutil.parser
import unicodedata
import time

In [13]:
os.environ['TOKEN'] = 'AAAAAAAAAAAAAAAAAAAAAAdYbAEAAAAArLyc5rCyuy0yIoRDlwFOqorZiKY%3DycgRhotZg0QsCDG00VH1LHVWkFWxatItAzp5qlLeuPyVikwdvG'
def auth():
    return os.getenv('TOKEN')
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers